!pip install numpy==1.26.3

# 베이스라인 정리
### 1. NeuralLDA(AVITM)
### 2. CTM
### 3. ClusterTM
### 4. Top2vec
### 5. LDA
### 6. BERTopic

In [1]:
import os

# 원하는 저장 경로를 변수에 저장 
desired_cache_path = "/mnt/ssd1/don_ssd1/twitter_crawling_don/UTopic/hub" # 본인 mnt 디렉토리 주소 입력

# TRANSFORMERS_CACHE 환경변수 설정
os.environ["TRANSFORMERS_CACHE"] = desired_cache_path

In [2]:
import os
import re
import string
from tqdm import tqdm
import numpy as np
import torch
from torch.utils.data import Dataset
from transformers import AutoTokenizer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.stem import WordNetLemmatizer
from sentence_transformers import SentenceTransformer
from data import *
from data import TwitterDataset, RedditDataset, YoutubeDataset, BertDataset
from coherence import get_topic_coherence

import pandas as pd
import torch.nn.functional as F
from sklearn.metrics import mutual_info_score
from torch.utils.data import DataLoader

import re
import os
import time
import argparse
import string
import torch
import torch.nn as nn
import torch.nn.functional as F
import gensim.downloader
import itertools

from sentence_transformers import SentenceTransformer

import numpy as np
from tqdm import tqdm_notebook
from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer
from sklearn.datasets import fetch_20newsgroups
from nltk.corpus import stopwords

from utils import AverageMeter

import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import mutual_info_score
from gensim.corpora.dictionary import Dictionary
from pytorch_transformers import *
import scipy.stats

from gensim.models.coherencemodel import CoherenceModel
from tqdm import tqdm
import nltk

from datetime import datetime
import gensim.downloader
from scipy.linalg import qr
from data import *
from sklearn.datasets import fetch_20newsgroups
from model import ContBertTopicExtractorAE

import random
from sklearn.metrics.pairwise import cosine_similarity

import warnings
warnings.filterwarnings("ignore")

%load_ext autoreload
%autoreload 2

[nltk_data] Downloading package punkt to /home/don12/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/don12/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/don12/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
args_text = '--base-model sentence-transformers/paraphrase-MiniLM-L6-v2 ' + \
            '--dataset all --n-word 30000 ' + \
            '--bsz 32 --stage-2-lr 2e-2 --stage-2-repeat 5 ' + \
            '--n-cluster 20 '

In [4]:
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "0,1" 

In [5]:
def _parse_args():
    parser = argparse.ArgumentParser(description='Contrastive topic modeling')

    #각 stage에서의 batch size
    parser.add_argument('--bsz', type=int, default=64,
                        help='Batch size')
    #data set정의 
    parser.add_argument('--dataset', default='twitter', type=str,
                        choices=['twitter', 'reddit', 'youtube','all'],
                        help='Name of the dataset')
    # 클러스터 수와 topic의 수는 20 (k==20)
    parser.add_argument('--n-cluster', default=20, type=int,
                        help='Number of clusters')
    parser.add_argument('--n-topic', type=int,
                        help='Number of topics. If not specified, use same value as --n-cluster')
    # 단어vocabulary는 2000로 setting
    parser.add_argument('--n-word', default=30000, type=int,
                        help='Number of words in vocabulary')
    
    parser.add_argument('--base-model', type=str,
                        help='Name of base model in huggingface library.')
    
    parser.add_argument('--gpus', default=[0,1,2,3], type=int, nargs='+',
                        help='List of GPU numbers to use. Use 0 by default')
   
    parser.add_argument('--dirichlet-alpha-1', type=float,
                        help='Parameter for Dirichlet distribution (Phase 1). Use 1/n_topic by default.')
 
    parser.add_argument('--coeff-2-recon', default=1.0, type=float,
                        help='Coefficient for VAE reconstruction loss (Phase 2)')
    parser.add_argument('--coeff-2-regul', default=1.0, type=float,
                        help='Coefficient for VAE KLD regularization loss (Phase 2)')
    parser.add_argument('--coeff-2-cons', default=1.0, type=float,
                        help='Coefficient for CL consistency loss (Phase 2)')
    parser.add_argument('--coeff-2-dist', default=1.0, type=float,
                        help='Coefficient for CL SWD distribution matching loss (Phase 2)')
    parser.add_argument('--dirichlet-alpha-2', type=float,
                        help='Parameter for Dirichlet distribution (Phase 2). Use same value as dirichlet-alpha-1 by default.')
    parser.add_argument('--stage-2-lr', default=2e-1, type=float,
                        help='Learning rate of phase 2')
    
    parser.add_argument('--stage-2-repeat', default=5, type=int,
                        help='Repetition count of phase 2')
    
    parser.add_argument('--result-file', type=str,
                        help='File name for result summary')
    
    
    # Check if the code is run in Jupyter notebook
    is_in_jupyter = False
    try:
        shell = get_ipython().__class__.__name__
        if shell == 'ZMQInteractiveShell':
            is_in_jupyter = True   # Jupyter notebook or qtconsole
        elif shell == 'TerminalInteractiveShell':
            is_in_jupyter = False  # Terminal running IPython
        else:
            is_in_jupyter = False  # Other type (?)
    except NameError:
        is_in_jupyter = False
    
    if is_in_jupyter:
        return parser.parse_args(args=args_text.split())
    else:
        return parser.parse_args()

In [6]:
device = torch.device("cuda:3" if torch.cuda.is_available() else "cpu")

In [85]:
def map_topics_to_labels(targets, target_names):

    topic_to_label = {
        'talk.politics.guns': 'politics',
        'talk.politics.mideast': 'politics',
        'talk.politics.misc': 'politics',
        'rec.sport.baseball': 'sport',
        'rec.sport.hockey': 'sport',
        'comp.os.ms-windows.misc': 'tech',
        'comp.sys.ibm.pc.hardware': 'tech',
        'comp.sys.mac.hardware': 'tech',
        'comp.windows.x': 'tech'
    }
    labels = np.array([topic_to_label.get(target_names[target], "other") for target in targets])
    return labels

def filter_documents(documents, labels, valid_labels):
    valid_indices = [i for i, label in enumerate(labels) if label in valid_labels]
    filtered_documents = [documents[i] for i in valid_indices]
    filtered_labels = [labels[i] for i in valid_indices]
    return filtered_documents, filtered_labels

# 20newsgroups 데이터셋 불러오기
dataset = fetch_20newsgroups(subset='all', remove=('headers', 'footers', 'quotes'))

documents = dataset.data
targets = dataset.target
target_names = dataset.target_names

for i in range(len(target_names)):
    doc_indices = np.where(targets == i)[0]
    doc_idx = doc_indices[0]

# 20newsgroups 데이터셋의 타겟을 'politics', 'sport', 'tech' 라벨로 매핑
mapped_labels = map_topics_to_labels(targets, target_names)

# 'politics', 'sport', 'tech' 라벨을 가진 문서 필터링
valid_labels = ['politics', 'sport', 'tech']
filtered_documents, filtered_labels = filter_documents(documents, mapped_labels, valid_labels)

# 필터링된 데이터를 DataFrame으로 변환
df_filtered = pd.DataFrame({
    'document': filtered_documents,
    'label': filtered_labels
})

In [9]:
nyt_df = pd.read_csv('nyt-articles-2020.csv')
newsdesk_to_label = {
    'Science': 'tech',
    'Technology': 'tech',
    'Business': 'tech',
    'Sports': 'sport',
    'OpEd': 'politics',
    'U.S.': 'politics',
    'New York': 'politics',
    'Politics': 'politics'
}

nyt_df['label'] = nyt_df['newsdesk'].map(newsdesk_to_label)

# 'politics', 'sport', 'tech' 라벨을 가진 행만 필터링
filtered_nyt_df = nyt_df[nyt_df['label'].isin(['politics', 'sport', 'tech'])]

In [10]:
import os
import pandas as pd

data_folder_path = '/mnt/ssd1/don_ssd1/twitter_crawling_don/UTopic/data/bbc'
labels = ['politics', 'sport', 'tech']

data = []
for label in labels:
    folder_path = os.path.join(data_folder_path, label)
    for filename in os.listdir(folder_path):
        file_path = os.path.join(folder_path, filename)
        with open(file_path, 'r', encoding='utf-8') as file:
            content = file.read()
            data.append({'label': label, 'document': content})

df = pd.DataFrame(data)

In [11]:
random.seed(42)

newsgroups_data = list(zip(df_filtered['document'].tolist(), df_filtered['label'].tolist()))
nyt_data = list(zip(filtered_nyt_df['abstract'].tolist(), filtered_nyt_df['label'].tolist()))
bbc_data = list(zip(df['document'].tolist(), df['label'].tolist()))

total_sample_size = 3600
labels = ['politics', 'sport', 'tech']
platforms = ['20newsgroups', 'nyt', 'bbc']
samples_per_label = total_sample_size // len(labels)

# 데이터와 라벨, 플랫폼을 라벨별로 분리하여 저장하는 함수
def sample_by_label(data, label, num_samples, platform):
    filtered_data = [(text, lbl, platform) for text, lbl in data if lbl == label]
    return random.sample(filtered_data, min(num_samples, len(filtered_data)))

# 데이터를 훈련과 테스트로 분할하는 함수
def split_train_test(data, train_ratio=0.8):
    train_size = int(len(data) * train_ratio)
    return data[:train_size], data[train_size:]

# 훈련 데이터에서 검증 데이터 분리하는 함수
def split_train_valid(data, valid_ratio_from_train=0.1):
    valid_size = int(len(data) * valid_ratio_from_train)
    train_size = len(data) - valid_size
    return data[:train_size], data[train_size:]

train_total_text_list = []
train_total_label_list = []
valid_total_text_list = []
valid_total_label_list = []
test_total_text_list = []
test_total_label_list = []
train_total_platform_list = []
valid_total_platform_list = []
test_total_platform_list = []

# 각 데이터셋에 대해 라벨별로 샘플링
data_sources = [(newsgroups_data, '20newsgroups'), (nyt_data, 'nyt'), (bbc_data, 'bbc')]

for label in labels:
    for data, platform in data_sources:
        sampled_data = sample_by_label(data, label, samples_per_label // len(platforms), platform)
        # 훈련 및 테스트 데이터 분할
        train_data, test_data = split_train_test(sampled_data)
        # 훈련 데이터에서 검증 데이터 분리
        train_data, valid_data = split_train_valid(train_data)

        train_total_text_list.extend([text for text, lbl, plt in train_data])
        train_total_label_list.extend([lbl for text, lbl, plt in train_data])
        train_total_platform_list.extend([plt for text, lbl, plt in train_data])
        valid_total_text_list.extend([text for text, lbl, plt in valid_data])
        valid_total_label_list.extend([lbl for text, lbl, plt in valid_data])
        valid_total_platform_list.extend([plt for text, lbl, plt in valid_data])
        test_total_text_list.extend([text for text, lbl, plt in test_data])
        test_total_label_list.extend([lbl for text, lbl, plt in test_data])
        test_total_platform_list.extend([plt for text, lbl, plt in test_data])


In [12]:
class BertDataset(Dataset):
    def __init__(self, bert, text_list, platform_label, label_list, N_word, vectorizer=None, lemmatize=False):
        self.lemmatize = lemmatize
        self.nonempty_text = [text for text in text_list if len(text) > 0]
        
        # Remove new lines
        self.nonempty_text = [re.sub("\n"," ", sent) for sent in self.nonempty_text]
                
        # Remove Emails
        self.nonempty_text = [re.sub('\S*@\S*\s?', '', sent) for sent in self.nonempty_text]
        
        # Remove new line characters
        self.nonempty_text = [re.sub('\s+', ' ', sent) for sent in self.nonempty_text]
        
        # Remove distracting single quotes
        self.nonempty_text = [re.sub("\'", "", sent) for sent in self.nonempty_text]
        
        
        self.jargons = set(['homosexual', 'simms', 'scsi', 'dma', 'ulf', 'color', 'armenian', 'widget', 'ide', 'centris', 'braves', 'leafs', 'faq', 'simm', 'gm', 'ethernet', 'stats', 'font', 'espn', 'meg', 'rgb', 'vram', 'buffalo', 'batf', 'printer', 'cpu', 'com', 'bruins', 'toronto', 'armenians', 'gant', 'lebanese', 'pitching', 'koresh', 'icon', 'dos', 'baerga', 'arabs', 'sabres', 'mb', 'dx', 'ottawa', 'azerbaijan', 'mailing', 'bitmap', 'norton', 'jews', 'gif', 'slave', 'pocklington', 'mhz', 'rectum', 'don', 'cdrom', 'ihr', 'irq', 'gld', 'cleveland', 'quadra', 'cursor', 'flames', 'bios', 'runs', 'wings', 'dl', 'penguins', 'motherboard', 'hp', 'gay', 'alomar', 'davidians', 'dale', 'colormap', 'israel', 'shrill', 'mattingly', 'pitcher', 'xr', 'chipset', 'diamond', 'cubs', 'detroit', 'fuhr', 'ordonly', 'floppy', 'gritz', 'sandberg', 'yankees', 'arab', 'clinton', 'controller', 'oh', 'vga', 'xman', 'hey', 'blasphemy', 'farrs', 'bosnia', 'wondering', 'libxmulibxmua', 'trumps', 'covid', 'biden', 'trump', 'vaccine', 'republicans', 'stock', 'outbreak', 'quarterback', 'chiefs', 'nfl', 'bidens', 'quarantine', 'lockdown', 'twitter', 'patriots', 'bowl', 'cancellation', 'facebook', 'ravens', 'steelers', 'canceled', 'soccer', 'woods', 'progressive', 'immune', 'pandemic', 'nba', 'colts', 'infection', 'gauff', 'vicepresidential', 'hospitalized', 'caucus', 'lawmaker', 'buttigieg', 'antibody', 'basketball', 'postseason', 'viral', 'blessing', 'marshmallow', 'ncaa', 'genetic', 'bernie', 'cheating', 'confront', 'djokovic', 'kentucky', 'bloombergs', 'pelicans', 'mate', 'distancing', 'floyds', 'patient', 'seahawks', 'pga', 'nomination', 'mds', 'tokyo', 'upended', 'biotech', 'lakers', 'immunity', 'shutdown', 'clinical', 'presidentelect', 'obama', 'scientist', 'readers', 'presidential', 'mlb', 'columnist', 'mask', 'furlough', 'republican', 'obsessing', 'donald', 'sanders', 'narrative', 'indistinguishable', 'astros', 'gym', 'coronavirus', 'apex', 'uncertainty', 'normalcy', 'miami', 'tennessee', 'rays', 'jacksonville', 'nominee', 'insect', 'alarmist', 'bee', 'safely', 'instagram', 'michigan', 'expanded', 'amazon', 'ukip', 'blog', 'patent', 'kenteris', 'mourinho', 'henman', 'moya', 'kilroysilk', 'gerrard', 'mirza', 'spam', 'thanou', 'wenger', 'souness', 'commodore', 'uwb', 'holmes', 'benitez', 'conte', 'bittorrent', 'blunkett', 'mock', 'spyware', 'ds', 'liverpool', 'robot', 'hague', 'iaaf', 'domain', 'parry', 'roddick', 'eu', 'bluray', 'agassi', 'nintendo', 'bt', 'aragones', 'screensaver', 'asylum', 'lycos', 'argonaut', 'hunting', 'hewitt', 'capriati', 'donation', 'firefox', 'sec', 'cabir', 'bnp', 'oleary', 'wifi', 'ferguson', 'safin', 'anelka', 'davenport', 'bellamy', 'blackpool', 'hiphop', 'robben', 'rfid', 'uefa', 'federer', 'drinking', 'skype', 'psp', 'radcliffe', 'cunningham', 'lions', 'hingis', 'straw', 'directive', 'dvd', 'ogara', 'ruddock', 'seafarer', 'hunt', 'browser', 'livingstone', 'seed', 'southampton', 'mcletchie', 'award', 'jaynes', 'poster', 'balco', 'referendum', 'edinburgh', 'hdtv', 'pension', 'indoor', 'mini', 'simonetti', 'grid', 'chepkemei', 'wilkinson', 'robinson', 'marathon', 'ink', 'dvds', 'chelsea'])
                
        self.tokenizer = AutoTokenizer.from_pretrained(bert)
        self.model = AutoModel.from_pretrained(bert)
        self.stopwords_list = set(TfidfVectorizer(stop_words="english").get_stop_words()).union(self.jargons)
        self.N_word = N_word
        
        if vectorizer == None:
            self.vectorizer = TfidfVectorizer(stop_words=None, max_features=self.N_word, token_pattern=r'\b[a-zA-Z]{2,}\b')
            self.vectorizer.fit(self.preprocess_ctm(self.nonempty_text))
        else:
            self.vectorizer = vectorizer
            
        self.org_list = []
        self.bow_list = []
        for sent in tqdm(self.nonempty_text):
            org_input = self.tokenizer(sent, padding='max_length', truncation=True, max_length=512, return_tensors='pt')
            org_input['input_ids'] = torch.squeeze(org_input['input_ids'])
            org_input['attention_mask'] = torch.squeeze(org_input['attention_mask'])
            self.org_list.append(org_input)
            self.bow_list.append(self.vectorize(sent))
        ## platform label    
        self.platform_label_list = platform_label
        self.label_list = label_list
            
        
    def vectorize(self, text):
        text = self.preprocess_ctm([text])
        vectorized_input = self.vectorizer.transform(text)
        vectorized_input = vectorized_input.toarray()
        vectorized_input = vectorized_input.astype(np.float64)

        # Get word distribution from BoW
        vectorized_input += 1e-8
        vectorized_input = vectorized_input / vectorized_input.sum(axis=1, keepdims=True)
        assert abs(vectorized_input.sum() - vectorized_input.shape[0]) < 0.01
        vectorized_label = torch.tensor(vectorized_input, dtype=torch.float)
        return vectorized_label[0]
        
        
    def preprocess_ctm(self, documents):
        preprocessed_docs_tmp = documents
        preprocessed_docs_tmp = [doc.lower() for doc in preprocessed_docs_tmp]
        preprocessed_docs_tmp = [doc.translate(
            str.maketrans(string.punctuation, ' ' * len(string.punctuation))) for doc in preprocessed_docs_tmp]
        preprocessed_docs_tmp = [' '.join([w for w in doc.split() if len(w) > 0 and w not in self.stopwords_list])
                             for doc in preprocessed_docs_tmp]
        if self.lemmatize:
            lemmatizer = WordNetLemmatizer()
            preprocessed_docs_tmp = [' '.join([lemmatizer.lemmatize(w) for w in doc.split()])
                                     for doc in preprocessed_docs_tmp]
        return preprocessed_docs_tmp    
    
    # mean_pooling 함수 정의
    def mean_pooling(self, model_output, attention_mask):
        input_mask_expanded = attention_mask.unsqueeze(-1).expand(model_output.size()).float()
        sum_embeddings = torch.sum(model_output * input_mask_expanded, 1)
        sum_mask = torch.clamp(input_mask_expanded.sum(1), min=1e-9)
        return sum_embeddings / sum_mask
    
    
    def __len__(self):
        return len(self.nonempty_text)
    

    def __getitem__(self, idx):
        sentence = self.nonempty_text[idx]
        encoded_input = self.tokenizer(sentence, padding=True, truncation=True, max_length=512, return_tensors='pt')
        
        with torch.no_grad():
            model_output = self.model(**encoded_input)
        
        # mean_pooling 함수를 사용하여 문장 임베딩의 평균을 계산
        pooled_embedding = self.mean_pooling(model_output.last_hidden_state, encoded_input['attention_mask'])

        # 임베딩과 attention mask 반환
        return self.org_list[idx], self.bow_list[idx], pooled_embedding, self.platform_label_list[idx], self.label_list[idx]


In [13]:
n_word = 30000
bert_name = "sentence-transformers/paraphrase-MiniLM-L6-v2"

In [14]:
trainds = BertDataset(bert=bert_name, text_list=train_total_text_list, platform_label=train_total_platform_list, label_list=train_total_label_list, N_word=n_word, vectorizer=None, lemmatize=True)
valds = BertDataset(bert=bert_name, text_list=valid_total_text_list, platform_label=valid_total_platform_list, label_list=valid_total_label_list, N_word=n_word, vectorizer=None, lemmatize=True)
testds = BertDataset(bert=bert_name, text_list=test_total_text_list, platform_label=test_total_platform_list, label_list=test_total_label_list, N_word=n_word, vectorizer=None, lemmatize=True)

2024-03-16 17:55:02.658615: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-03-16 17:55:02.868898: I tensorflow/core/util/port.cc:104] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-03-16 17:55:03.887865: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda-11.7/lib64:
2024-03-16 17:55:03.888007: W tensorflow/compiler/xla/strea

In [15]:
# 테스트 데이터에서 문서 전처리
reference_corpus = [doc.split() for doc in testds.preprocess_ctm(testds.nonempty_text)]
platform_labels = testds.platform_label_list  # 각 문서의 플랫폼 정보

platform_corpora = {'bbc': [], 'nyt': [], '20newsgroups': []}

# 각 문서를 플랫폼 정보에 따라 분류
for doc, platform in zip(reference_corpus, platform_labels):
    if platform in platform_corpora:
        platform_corpora[platform].append(doc)

bbc_texts = platform_corpora['bbc']
nyt_texts = platform_corpora['nyt']
news_texts = platform_corpora['20newsgroups']

# 각 플랫폼 별 문서 수 확인
print(f"'bbc' 문서 수: {len(bbc_texts)}")
print(f"'nyt' 문서 수: {len(nyt_texts)}")
print(f"'20newsgroups' 문서 수: {len(news_texts)}")

'bbc' 문서 수: 238
'nyt' 문서 수: 240
'20newsgroups' 문서 수: 240


# AVITM(Autoencoding Variational Inference For Topic Models)

### 참조 : https://arxiv.org/abs/1703.01488
### Github : https://github.com/akashgit/autoencoding_vi_for_topic_models

In [16]:
from pytorchavitm.datasets import BOWDataset
from pytorchavitm.avitm import AVITM

# BoW 벡터를 BOWDataset에 적용
# BoW 벡터 추출
bow_vectors = [trainds[i][1] for i in range(len(trainds))]

# BOWDataset 인스턴스 생성
bow_dataset = BOWDataset(bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# AVITM 모델 학습
input_size = len(trainds.vectorizer.get_feature_names_out())  # 또는 적절한 입력 크기
avitm = AVITM(input_size=input_size, n_components=20)
# 모델 초기화 및 학습
# avitm = AVITM(input_size=n_word, n_components=20)  # 필요한 하이퍼파라미터 설정
avitm.fit(bow_dataset)

# 토픽 추출 및 평가
# 토픽 추출
topics = avitm.get_topics(10)  # 각 토픽별로 상위 10개 단어 추출

# 리스트 생성
avitm_topics = []
for topic_num, words in topics.items():
    avitm_topics.append((topic_num, words))

# 결과 출력
for topic_num, words in avitm_topics:
    print(f"Topic {topic_num}: {words}")

Settings: 
               N Components: 20
               Topic Prior Mean: 0.0
               Topic Prior Variance: 0.95
               Model Type: prodLDA
               Hidden Sizes: (100, 100)
               Activation: softplus
               Dropout: 0.2
               Learn Priors: True
               Learning Rate: 0.002
               Momentum: 0.99
               Reduce On Plateau: False
               Save Dir: None
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	-

In [20]:
# Assuming test_total_text_list contains your raw test documents
test_texts = [' '.join(doc.split()) for doc in test_total_text_list]  # Adjust this line according to your data preprocessing steps


In [18]:
import numpy as np
import pandas as pd
import torch
from torch.utils.data import DataLoader
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋 준비
# test_bow_vectors = trainds.vectorizer.transform(test_texts)
# test_bow_dataset = BOWDataset(test_bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

test_bow_vectors = trainds.vectorizer.transform(test_texts).toarray()

# 변환된 벡터를 사용하여 BOWDataset 인스턴스 생성
test_bow_dataset = BOWDataset(test_bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# 테스트 데이터셋에 대한 토픽 분포 예측
test_topic_distributions = avitm.predict(test_bow_dataset)

# 토픽 라벨 추출
test_topic_labels = torch.argmax(test_topic_distributions, dim=1).cpu().numpy()

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

ValueError: Found input variables with inconsistent numbers of samples: [720, 718]

In [22]:
# 테스트 데이터셋 준비
bow_vectors = [trainds[i][1] for i in range(len(trainds))]
bow_dataset = BOWDataset(bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# 테스트 데이터셋에 대한 토픽 분포 예측
topic_distributions = avitm.predict(bow_dataset)

# # 토픽 라벨 추출
# test_topic_labels = np.argmax(test_topic_distributions, axis=1)
# PyTorch의 argmax 메소드 사용 (GPU 상에서 직접 작업 가능)
topic_labels = torch.argmax(topic_distributions, dim=1)

# PyTorch 텐서를 CPU로 이동시킨 후 NumPy 배열로 변환
topic_labels_cpu = topic_labels.cpu().numpy()

# 토픽별 라벨 데이터 수집
topic_labels_avitm = [[] for _ in range(avitm.n_components)]  # avitm.n_components는 AVITM 모델에서 설정한 토픽 수

for doc_idx, topic in enumerate(topic_labels_cpu):
    label = train_total_label_list[doc_idx]  # 각 문서에 해당하는 실제 라벨
    topic_labels_avitm[topic].append(label)
    
# 토픽별 라벨 데이터 수집
topic_labels_avitm = [[] for _ in range(avitm.n_components)]  # avitm.n_components는 AVITM 모델에서 설정한 토픽 수

for doc_idx, topic in enumerate(topic_labels_cpu):
    label = train_total_label_list[doc_idx]  # 각 문서에 해당하는 실제 라벨
    topic_labels_avitm[topic].append(label)

# 라벨 퓨리티 계산
def calculate_label_purity(topic_labels):
    purity_scores = []
    for labels in topic_labels:
        if not labels:
            continue
        most_common_label = max(set(labels), key=labels.count)
        purity = labels.count(most_common_label) / len(labels)
        purity_scores.append(purity)
    average_purity = sum(purity_scores) / len(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# label purity 계산
purity_scores_avitm, average_purity_avitm = calculate_label_purity(topic_labels_avitm)

print("AVITM 각 토픽의 라벨 순도:", purity_scores_avitm)
print("AVITM 평균 라벨 순도:", average_purity_avitm)


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

# 헝가리안 매칭

In [118]:
# 헝가리안 매칭을 위한 함수 정의
def measure_hungarian_score(topic_dist, train_target):
    dist = topic_dist
    train_target_filtered = train_target
    flat_predict = torch.tensor(np.argmax(dist, axis=1))
    flat_target = torch.tensor(train_target_filtered).to(flat_predict.device)
    num_samples = flat_predict.shape[0]
    num_classes = dist.shape[1]
    match = _hungarian_match(flat_predict, flat_target, num_samples, num_classes)    
    reordered_preds = torch.zeros(num_samples).to(flat_predict.device)
    for pred_i, target_i in match:
        reordered_preds[flat_predict == pred_i] = int(target_i)
    acc = int((reordered_preds == flat_target.float()).sum()) / float(num_samples)
    return acc


# # 헝가리안 매칭을 위한 함수 정의
# def measure_hungarian_score(dist, true_labels):
#     num_samples = len(true_labels)
#     num_classes = len(np.unique(true_labels))
#     flat_predict = np.argmax(dist, axis=1)
#     matrix = np.zeros((num_classes, num_classes), dtype=np.uint64)
#     for i in range(num_samples):
#         matrix[flat_predict[i], true_labels[i]] += 1
#     row_ind, col_ind = linear_sum_assignment(matrix.max() - matrix)
#     match = list(zip(row_ind, col_ind))
#     reordered_preds = np.zeros(num_samples, dtype=int)
#     for pred_i, target_i in match:
#         reordered_preds[flat_predict == pred_i] = target_i
#     acc = np.sum(reordered_preds == true_labels) / float(num_samples)
#     return acc

def _hungarian_match(predicted, target, num_samples, num_classes):
    matrix = np.zeros((num_classes, num_classes), dtype=np.uint64)
    for i in range(num_samples):
        matrix[predicted[i], target[i]] += 1
    row_ind, col_ind = linear_sum_assignment(matrix.max() - matrix)

In [119]:
from pytorchavitm.datasets import BOWDataset
from pytorchavitm.avitm import AVITM
import numpy as np
import torch
from torch.utils.data import DataLoader
from scipy.optimize import linear_sum_assignment
import torch.nn.functional as F

# 데이터 로딩 및 전처리
bow_vectors = [trainds[i][1] for i in range(len(trainds))]
bow_dataset = BOWDataset(bow_vectors, idx2token=trainds.vectorizer.get_feature_names_out())

# AVITM 모델 학습
input_size = len(trainds.vectorizer.get_feature_names_out())  # 입력 크기 설정
avitm = AVITM(input_size=input_size, n_components=3)  # 토픽의 개수를 3으로 설정
avitm.fit(bow_dataset)  # 모델 학습

# 토픽 추출 및 평가
topics = avitm.get_topics(10)  # 각 토픽별로 상위 10개 단어 추출
avitm_topics = []
for topic_num, words in topics.items():
    avitm_topics.append((topic_num, words))
for topic_num, words in avitm_topics:
    print(f"Topic {topic_num}: {words}")



Settings: 
               N Components: 3
               Topic Prior Mean: 0.0
               Topic Prior Variance: 0.6666666666666667
               Model Type: prodLDA
               Hidden Sizes: (100, 100)
               Activation: softplus
               Dropout: 0.2
               Learn Priors: True
               Learning Rate: 0.002
               Momentum: 0.99
               Reduce On Plateau: False
               Save Dir: None
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork i

In [125]:
test_bow_vectors = [testds[i][1] for i in range(len(testds))]
test_bow_dataset = BOWDataset(test_bow_vectors, idx2token=testds.vectorizer.get_feature_names_out())


# 테스트 데이터셋의 토픽 분포 추출
test_topic_distributions = avitm.transform(test_bow_dataset)

# 테스트 데이터 라벨
test_labels = [testds[i][2] for i in range(len(testds))]  # testds의 구조에 따라 인덱스 조정 필요

# 라벨을 정수로 매핑
label_to_int = {label: idx for idx, label in enumerate(sorted(set(test_labels)))}
int_test_labels = np.array([label_to_int[label] for label in test_labels])


# 정확도 계산
accuracy = measure_hungarian_score(test_topic_distributions, int_test_labels)
print(f"Test Accuracy with Hungarian Matching: {accuracy}")


AttributeError: 'Tensor' object has no attribute 'toarray'

# AVITM coherence

In [23]:
topics = avitm_topics

In [24]:
# 제공된 topics 튜플 리스트를 단순한 리스트 형태로 변환하는 코드
def convert_topics_to_list(topics):
    return [words for _, words in topics]

# 함수 호출
topics = convert_topics_to_list(topics)

## BBC

In [28]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.13845204958615895, 'UCI': 0.4542725204932986, 'UMASS': -1.7660057565461167, 'CV': 0.5299923955530974, 'Topic_Diversity': 0.69}


## NYT

In [29]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.584716024824645, 'UCI': 3.1176366490299188, 'UMASS': -1.2373817472117155, 'CV': 0.6795449126022008, 'Topic_Diversity': 0.69}


## Newsgroup

In [30]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.2892964007125206, 'UCI': 1.4456191303374892, 'UMASS': -1.8837279172471102, 'CV': 0.5979242705102985, 'Topic_Diversity': 0.69}


# CTM(Contextualized Topic Models)

### 참조 : https://aclanthology.org/2021.acl-short.96/
### Github : https://github.com/MilaNLProc/contextualized-topic-models?tab=readme-ov-file

In [31]:
from contextualized_topic_models.models.ctm import CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation
train_total_text_list
# CTM 데이터 준비
tp = TopicModelDataPreparation("stsb-distilbert-base")
training_dataset = tp.fit(text_for_contextual=train_total_text_list, text_for_bow=train_total_text_list)

# CTM 모델 생성 및 학습
n_topic = 20 # 토픽의 수 설정
ctm = CombinedTM(bow_size=len(tp.vocab), contextual_size=768, n_components=n_topic, num_epochs=20)
ctm.fit(training_dataset)

# 토픽의 상위 k개 단어 추출
top_k = 10
ctm_topics = ctm.get_topic_lists(top_k)
for topic_num, topic in enumerate(ctm_topics):
    print(f"Topic {topic_num}: {topic}")


Batches:   0%|          | 0/13 [00:00<?, ?it/s]

0it [00:00, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Epoch: [1/20]	 Seen Samples: [2560/51840]	Train Loss: 2237.5971099853514	Time: 0:00:06.583664: : 1it [00:06,  6.58s/it]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

...

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

 90%|█████████ | 37/41 [00:05<00:00, 12.96it/s]

	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 41/41 [00:06<00:00,  6.60it/s]

Topic 0: ['used', 'more', 'make', 'its', 'also', 'than', 'about', 'computer', 'said', 'some']
Topic 1: ['win', 'first', 'back', 'half', 'three', 'second', 'side', 'england', 'williams', 'match']
Topic 2: ['please', 'nor', 'owner', 'correctly', 'advance', 'seems', 'disk', 'curfew', 'xreparentwindow', 'pogrom']
Topic 3: ['teenagers', 'mention', 'battlefront', 'properties', 'absolute', 'route', 'element', 'elements', 'pilot', 'headquarters']
Topic 4: ['technology', 'users', 'million', 'its', 'according', 'mobile', 'more', 'computer', 'software', 'than']
Topic 5: ['removed', 'innocent', 'bloggers', 'obsessed', 'follows', 'arrangements', 'catch', 'shame', 'aspects', 'lawyers']
Topic 6: ['mike', '16', '11', 'ken', 'rangers', 'pit', 'gary', 'phi', '253', '19']
Topic 7: ['removed', 'hopkins', 'follows', 'slightly', 'arash', 'mojtaba', 'widows', 'teenagers', 'iranian', 'addicted']
Topic 8: ['the', 'with', 'to', 'of', 'and', 'in', 'have', 'on', 'it', 'is']
Topic 9: ['bloggers', 'visiting', 'hopk

In [33]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋 준비 및 토픽 분포 추출
test_dataset = tp.transform(text_for_contextual=test_total_text_list, text_for_bow=test_total_text_list)
test_topic_distributions = ctm.get_thetas(test_dataset)

# 토픽 라벨 추출
test_topic_labels = np.argmax(test_topic_distributions, axis=1)

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)



Batches:   0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/12 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

  8%|▊         | 1/12 [00:06<01:08,  6.19s/it]

	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 12/12 [00:06<00:00,  1.80it/s]


Normalized Mutual Information (NMI): 0.16768231185967067
H(Y): 2.930020133032206
H(Y|X): 2.592255585143689
Mutual Information (MI): 0.3377645478885172


ValueError: Found input variables with inconsistent numbers of samples: [720, 718]

In [35]:
def assign_topics_to_documents_ctm(ctm_model, dataset):
    topic_assignments = []
    # 모든 문서에 대한 토픽 분포를 얻음
    topic_distributions = ctm_model.get_thetas(dataset)
    
    # 가장 확률이 높은 토픽을 선택
    for doc_distribution in topic_distributions:
        assigned_topic = doc_distribution.argmax()
        topic_assignments.append(assigned_topic)
    
    return topic_assignments
# 문서에 대한 토픽 할당
document_topics_ctm = assign_topics_to_documents_ctm(ctm, training_dataset)

# 토픽별 라벨 데이터 수집
topic_labels_ctm = [[] for _ in range(n_topic)]
for doc_idx, topic in enumerate(document_topics_ctm):
    label = train_total_label_list[doc_idx]  # 문서에 해당하는 라벨
    topic_labels_ctm[topic].append(label)

# 라벨 순도 계산
purity_scores_ctm, average_purity_ctm = calculate_label_purity(topic_labels_ctm)

print("CTM 각 토픽의 라벨 순도:", purity_scores_ctm)
print("CTM 평균 라벨 순도:", average_purity_ctm)


  0%|          | 0/41 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

 88%|████████▊ | 36/41 [00:06<00:00, 11.69it/s]

	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


100%|██████████| 41/41 [00:06<00:00,  5.86it/s]

CTM 각 토픽의 라벨 순도: [0.5384615384615384, 0.9695121951219512, 0.38513513513513514, 0.3671875, 0.9631578947368421, 0.4, 0.6728971962616822, 0.37404580152671757, 0.6403508771929824, 0.3893129770992366, 0.9830508474576272, 0.9346153846153846, 0.3418803418803419, 0.35365853658536583, 0.4240506329113924, 0.6363636363636364, 0.7924528301886793, 0.7131147540983607, 0.6, 0.6111111111111112]
CTM 평균 라벨 순도: 0.6045179595373992


# CTM coherence

In [36]:
topics = ctm_topics

## BBC

In [38]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.34426686735321954, 'UCI': 1.4833910431755082, 'UMASS': -1.3819162418785473, 'CV': 0.7414584462584844, 'Topic_Diversity': 0.82}


## NYT

In [39]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.6995770584922866, 'UCI': 3.81450863472656, 'UMASS': -0.914820527473115, 'CV': 0.79841100325982, 'Topic_Diversity': 0.82}


## News

In [40]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.4311937197826451, 'UCI': 2.2466634522601954, 'UMASS': -1.4434114393720339, 'CV': 0.7138270352216208, 'Topic_Diversity': 0.82}


# ClusterTM

### 참조 : https://aclanthology.org/2020.emnlp-main.135/
### Github : https://github.com/adalmia96/Cluster-Analysis

In [43]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
import numpy as np

# 전처리된 문서 리스트 (예: train_total_text_list)
documents = train_total_text_list

# TF-IDF 벡터 생성
tfidf_vectorizer = TfidfVectorizer(stop_words='english')
tfidf_matrix = tfidf_vectorizer.fit_transform(documents)

# KMeans 클러스터링 수행
n_clusters = 20
kmeans = KMeans(n_clusters=n_clusters, random_state=0)
kmeans.fit(tfidf_matrix)

# 각 클러스터의 대표 단어 추출
order_centroids = kmeans.cluster_centers_.argsort()[:, ::-1]
terms = tfidf_vectorizer.get_feature_names_out()

cluster_topics = []
for i in range(n_clusters):
    top_words = [terms[ind] for ind in order_centroids[i, :10]]
    cluster_topics.append(top_words)
    print(f"Cluster {i}: {top_words}")


Cluster 0: ['pandemic', 'coronavirus', 'sports', 'online', 'world', 'americans', 'era', 'surged', 'trouble', 'homebound']
Cluster 1: ['coronavirus', 'new', 'president', 'time', 'biden', 'just', 'said', 'years', 'states', 'virus']
Cluster 2: ['said', 'users', 'people', 'software', 'net', 'spam', 'search', 'site', 'web', 'computer']
Cluster 3: ['chelsea', 'united', 'arsenal', 'club', 'liverpool', 'said', 'manchester', 'league', 'ferguson', 'manager']
Cluster 4: ['don', 'people', 'gun', 'right', 'israel', 'need', 'just', 'government', 'think', 'guns']
Cluster 5: ['stock', 'outbreak', 'coronavirus', 'business', 'market', 'latest', 'news', 'updates', 'live', 'zzzzzzt']
Cluster 6: ['microsoft', 'windows', 'dos', 'version', 'software', 'spyware', 'security', 'driver', 'programs', 'users']
Cluster 7: ['wales', 'williams', 'rugby', 'jones', 'welsh', 'england', 'france', 'nations', 'italy', 'said']
Cluster 8: ['eu', 'armenian', 'deal', 'country', 'armenians', 'straw', 'said', 'turkish', 'europea

In [44]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋 준비 및 클러스터 라벨 추출
test_tfidf_matrix = tfidf_vectorizer.transform(test_total_text_list)
test_topic_labels = kmeans.predict(test_tfidf_matrix)

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)

Normalized Mutual Information (NMI): 0.29771313147995837
H(Y): 2.2570398636480427
H(Y|X): 1.7575301645501815
Mutual Information (MI): 0.49950969909786114


ValueError: Found input variables with inconsistent numbers of samples: [720, 718]

In [45]:
# 문서의 클러스터 할당
document_clusters = kmeans.labels_

# 클러스터별 라벨 데이터 수집
cluster_labels = [[] for _ in range(n_clusters)]
for doc_idx, cluster_idx in enumerate(document_clusters):
    label = train_total_label_list[doc_idx]  # 문서에 해당하는 라벨
    cluster_labels[cluster_idx].append(label)

# 라벨 순도 계산 함수는 이전에 제공된 calculate_label_purity 함수를 그대로 사용합니다.

# 라벨 순도 계산
purity_scores_cluster, average_purity_cluster = calculate_label_purity(cluster_labels)

print("각 클러스터의 라벨 순도:", purity_scores_cluster)
print("평균 라벨 순도:", average_purity_cluster)


각 클러스터의 라벨 순도: [0.49122807017543857, 0.35374868004223864, 1.0, 0.9759036144578314, 0.7929292929292929, 1.0, 0.9743589743589743, 0.875, 0.7076923076923077, 1.0, 0.9523809523809523, 0.9864864864864865, 0.5783132530120482, 0.9463087248322147, 0.8478260869565217, 1.0, 1.0, 0.7582417582417582, 0.98989898989899, 0.948051948051948]
평균 라벨 순도: 0.8589184569758501


# ClusterTM coherence

In [46]:
topics = cluster_topics

## BBC

In [47]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.21762313873933622, 'UCI': 0.7954562431602398, 'UMASS': -1.4425081345449975, 'CV': 0.7344633264224595, 'Topic_Diversity': 0.825}


## NYT

In [48]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.505158630163769, 'UCI': 2.6560370703035248, 'UMASS': -1.1820251054551678, 'CV': 0.7071729249860288, 'Topic_Diversity': 0.825}


## News

In [49]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.3421672805085414, 'UCI': 1.669048286107763, 'UMASS': -1.5974709820722237, 'CV': 0.6488018839342369, 'Topic_Diversity': 0.825}


# Top2vec

!pip install numpy==1.24

In [53]:
from top2vec import Top2Vec
import random

np.random.seed(41)
random.seed(41)

# 트레인 데이터 로드
# 여기서는 train_total_text_list가 트레인 데이터의 텍스트 리스트라고 가정합니다.
documents = train_total_text_list

# Top2Vec 모델 학습
# speed='deep-learn'은 더 정확한 모델을 위해 더 많은 시간이 걸릴 수 있습니다.
# workers는 사용할 CPU 코어 수입니다. -1은 모든 코어를 사용한다는 의미입니다.
model = Top2Vec(documents, speed="deep-learn", workers=-1)

# 학습된 모델에서 20개의 토픽에 대한 상위 10개 토픽 워드 추출
topic_words, word_scores, topic_nums = model.get_topics(num_topics=20)

# 각 토픽별 워드 리스트를 저장할 빈 리스트 생성
top_10_word_lists = []

for words in topic_words:
    # 각 토픽에서 상위 10개 단어만 선택
    top_10_words = words[:10]
    top_10_word_lists.append(top_10_words)

# 결과 출력
for i, word_list in enumerate(top_10_word_lists):
    print(f"토픽 {i+1}의 상위 10개 워드:")
    print(word_list)
    print("\n")

2024-03-16 19:39:00,624 - top2vec - INFO - Pre-processing documents for training
INFO:top2vec:Pre-processing documents for training
2024-03-16 19:39:01,882 - top2vec - INFO - Downloading universal-sentence-encoder-multilingual model
INFO:top2vec:Downloading universal-sentence-encoder-multilingual model
2024-03-16 19:39:04,180 - top2vec - INFO - Creating joint document/word embedding
INFO:top2vec:Creating joint document/word embedding
2024-03-16 19:39:07,406 - top2vec - INFO - Creating lower dimension embedding of documents
INFO:top2vec:Creating lower dimension embedding of documents
2024-03-16 19:39:22,229 - top2vec - INFO - Finding dense areas of documents
INFO:top2vec:Finding dense areas of documents
2024-03-16 19:39:22,276 - top2vec - INFO - Finding topics
INFO:top2vec:Finding topics


토픽 1의 상위 10개 워드:
['parliament' 'politicians' 'ministers' 'election' 'elections' 'minister'
 'britain' 'conservatives' 'tories' 'voters']


토픽 2의 상위 10개 워드:
['broadband' 'technologies' 'microsoft' 'technology' 'spyware' 'sony'
 'gadgets' 'computers' 'uk' 'consumers']


토픽 3의 상위 10개 워드:
['windows' 'mac' 'hardware' 'software' 'microsoft' 'files' 'programs'
 'pcs' 'dvd' 'pc']


토픽 4의 상위 10개 워드:
['democrats' 'dems' 'election' 'democrat' 'elections' 'voters' 'president'
 'conservatives' 'politics' 'politicians']


토픽 5의 상위 10개 워드:
['league' 'sports' 'football' 'championship' 'baseball' 'hockey' 'stadium'
 'teams' 'sport' 'tournament']


토픽 6의 상위 10개 워드:
['viruses' 'coronavirus' 'research' 'virus' 'few' 'found' 'cases'
 'possible' 'evidence' 'revealed']


토픽 7의 상위 10개 워드:
['hockey' 'rangers' 'teams' 'tim' 'team' 'premiership' 'baseball'
 'championship' 'robinson' 'chelsea']


토픽 8의 상위 10개 워드:
['baseball' 'roddick' 'robinson' 'rangers' 'hockey' 'stadium'
 'championship' 'league' 'teams' 'rugby

In [54]:
# 테스트 데이터에 대한 토픽 라벨과 점수를 얻기 위한 코드

# 빈 리스트를 초기화하여 각 테스트 데이터 항목의 토픽 라벨과 점수를 저장
test_topic_labels = []
test_data_topic_scores = []

# 테스트 데이터셋의 각 항목에 대해 반복
for text in test_total_text_list:
    # query_topics 메소드를 사용하여 각 텍스트에 대한 토픽 검색
    # 여기서는 가장 관련 있는 한 개의 토픽만 찾습니다(num_topics=1)
    topics_words, word_scores, topic_scores, topic_nums = model.query_topics(query=text, num_topics=1)
    
    # 찾아낸 토픽 번호와 점수를 리스트에 추가
    if topic_nums.size > 0:  # 토픽이 하나 이상 찾아진 경우
        test_topic_labels.append(topic_nums[0])
        test_data_topic_scores.append(topic_scores[0])
    else:  # 토픽을 찾지 못한 경우
        test_topic_labels.append(None)
        test_data_topic_scores.append(0)

# # 결과 출력
# for i, (label, score) in enumerate(zip(test_data_topic_labels, test_data_topic_scores)):
#     print(f"테스트 데이터 {i+1}: 토픽 라벨 = {label}, 점수 = {score}")

In [55]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 가정: test_platform_labels는 준비되어 있음
# Top2Vec 모델을 사용하여 각 문서의 토픽 라벨을 추출합니다 (여기서는 이미 추출되어 있다고 가정)

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 플랫폼별 및 전체에 대한 토픽 분포를 계산
platform_counts = pd.Series(test_platform_labels).value_counts()
platform_probabilities = platform_counts / platform_counts.sum()

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 및 정규화된 상호정보량(NMI) 계산
mi = H_Y - H_Y_given_X_total
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)

# # sklearn의 mutual_info_score를 사용하여 직접 MI 계산
# mi_score = mutual_info_score(test_topic_labels, test_platform_labels)
# print("Original Mutual Information Score:", mi_score)


Normalized Mutual Information (NMI): 0.43419615702091946
H(Y): 2.8616962949355895
H(Y|X): 2.001922597247227
Mutual Information (MI): 0.8597736976883623


In [57]:
from top2vec import Top2Vec
import logging

np.random.seed(41)
random.seed(41)

# 로깅 설정을 조정하여 Top2Vec의 내부 작업을 보다 자세히 볼 수 있습니다.
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

# 트레인 데이터 로드
documents = train_total_text_list  # train_total_text_list는 트레인 데이터의 텍스트 리스트입니다.

try:
    model = Top2Vec(documents, speed="deep-learn", workers=-1, 
                    umap_args={'n_neighbors': 25, 'n_components': 3, 'metric': 'cosine'}, 
                    hdbscan_args={'min_cluster_size': 10, 'metric': 'euclidean', 'cluster_selection_method': 'eom'})
except Exception as e:
    print(f"모델 학습 중 오류 발생: {e}")

# 학습된 모델에서 토픽 추출
# 추출된 토픽 수가 20개 미만일 경우, 추가 조정이 필요할 수 있습니다.
topic_words, word_scores, topic_nums = model.get_topics()

# 모델이 생성한 토픽 수를 확인하고, 20개 미만일 경우 로그나 경고 메시지 출력
print(f"모델이 생성한 토픽의 수: {len(topic_nums)}")
if len(topic_nums) < 20:
    print("경고: 요청한 20개의 토픽을 생성하지 못했습니다. 파라미터 조정이 필요할 수 있습니다.")

# 각 토픽별 워드 리스트를 저장할 빈 리스트 생성
top_10_word_lists = []

for words in topic_words:
    # 각 토픽에서 상위 10개 단어만 선택
    top_10_words = words[:10]
    top_10_word_lists.append(top_10_words)

# 결과 출력
for i, word_list in enumerate(top_10_word_lists):
    print(f"토픽 {i+1}의 상위 10개 워드:")
    print(word_list)
    print("\n")


2024-03-16 19:39:54,770 - top2vec - INFO - Pre-processing documents for training
INFO:top2vec:Pre-processing documents for training
2024-03-16 19:39:56,711 - top2vec - INFO - Downloading universal-sentence-encoder-multilingual model
INFO:top2vec:Downloading universal-sentence-encoder-multilingual model
2024-03-16 19:39:58,516 - top2vec - INFO - Creating joint document/word embedding
INFO:top2vec:Creating joint document/word embedding
2024-03-16 19:40:01,782 - top2vec - INFO - Creating lower dimension embedding of documents
INFO:top2vec:Creating lower dimension embedding of documents
2024-03-16 19:40:17,108 - top2vec - INFO - Finding dense areas of documents
INFO:top2vec:Finding dense areas of documents
2024-03-16 19:40:17,148 - top2vec - INFO - Finding topics
INFO:top2vec:Finding topics


모델이 생성한 토픽의 수: 20
토픽 1의 상위 10개 워드:
['democrats' 'dems' 'conservatives' 'election' 'voters' 'democrat'
 'politicians' 'elections' 'politics' 'president']


토픽 2의 상위 10개 워드:
['parliament' 'ministers' 'politicians' 'election' 'elections' 'minister'
 'britain' 'conservatives' 'tories' 'voters']


토픽 3의 상위 10개 워드:
['broadband' 'technologies' 'microsoft' 'technology' 'spyware' 'sony'
 'gadgets' 'computers' 'consumers' 'uk']


토픽 4의 상위 10개 워드:
['baseball' 'hockey' 'rangers' 'teams' 'robinson' 'tim' 'roddick'
 'stadium' 'championship' 'team']


토픽 5의 상위 10개 워드:
['windows' 'mac' 'hardware' 'software' 'microsoft' 'files' 'programs'
 'pcs' 'dvd' 'pc']


토픽 6의 상위 10개 워드:
['league' 'sports' 'football' 'championship' 'baseball' 'hockey' 'stadium'
 'teams' 'sport' 'tournament']


토픽 7의 상위 10개 워드:
['rugby' 'england' 'scotland' 'scottish' 'ireland' 'ferguson' 'rangers'
 'kilroy' 'premiership' 'robinson']


토픽 8의 상위 10개 워드:
['arsenal' 'liverpool' 'chelsea' 'manchester' 'premiership' 'united'
 'ferguson'

In [58]:
from collections import Counter

# 문서의 토픽 할당을 얻는 함수를 수정합니다.
def get_document_topic_assignments(model):
    # 모델에 저장된 모든 문서의 ID를 가져옵니다.
    document_ids = list(range(len(model.doc_top)))
    # 각 문서 ID에 대해 가장 관련이 높은 토픽을 조회합니다.
    doc_topics, doc_scores, topic_words, word_scores = model.get_documents_topics(doc_ids=document_ids, reduced=False)
    
    # 각 문서에 할당된 토픽 번호를 반환합니다.
    # doc_topics 자체가 각 문서에 할당된 토픽 번호의 배열이므로, 이를 직접 반환합니다.
    return doc_topics


# 문서에 할당된 토픽을 얻습니다.
document_topics = get_document_topic_assignments(model)

# 라벨 퓨리티를 계산하는 함수
def calculate_label_purity(documents, labels, document_topics):
    topic_label_mapping = [[] for _ in range(max(document_topics) + 1)]
    for doc_topic, label in zip(document_topics, labels):
        topic_label_mapping[doc_topic].append(label)
    
    purity_scores = []
    for topic_labels in topic_label_mapping:
        if topic_labels:
            most_common_label, count = Counter(topic_labels).most_common(1)[0]
            purity = count / len(topic_labels)
            purity_scores.append(purity)
    
    average_purity = sum(purity_scores) / len(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# 상위 20개 토픽에 대한 문서만 필터링 (상위 20개 토픽의 인덱스가 필요)
selected_topics = set(topic_nums[:20])
filtered_document_topics = [topic for topic in document_topics if topic in selected_topics]

# 라벨 퓨리티 계산
purity_scores, average_purity = calculate_label_purity(train_total_text_list, train_total_label_list, filtered_document_topics)

print("각 토픽의 라벨 퓨리티:", purity_scores)
print("평균 라벨 퓨리티:", average_purity)


각 토픽의 라벨 퓨리티: [0.5464135021097046, 0.9738562091503268, 0.9867109634551495, 0.9468085106382979, 0.9633699633699634, 0.8709677419354839, 0.9537037037037037, 0.978021978021978, 0.9382716049382716, 0.9090909090909091, 0.9552238805970149, 0.8412698412698413, 0.9, 0.9137931034482759, 0.7674418604651163, 0.37142857142857144, 0.7272727272727273, 0.96875, 0.8518518518518519, 0.9615384615384616]
평균 라벨 퓨리티: 0.8662892692142824


# Top2vec coherence

In [59]:
topics = top_10_word_lists

## BBC

In [60]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.2975914520477609, 'UCI': 1.2915150598501666, 'UMASS': -1.5477758070700471, 'CV': 0.6340418829033914, 'Topic_Diversity': 0.71}


## NYT

In [61]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.5809720285499865, 'UCI': 3.1390932749245737, 'UMASS': -0.9057598564090459, 'CV': 0.7587230672686736, 'Topic_Diversity': 0.71}


## News

In [62]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.5476931619538734, 'UCI': 2.837746136362161, 'UMASS': -1.038032253816287, 'CV': 0.684330312056445, 'Topic_Diversity': 0.71}


# LDA 

In [65]:

reference_dictionary = Dictionary(reference_corpus)
dictionary=reference_dictionary

In [66]:
from gensim.models import LdaMulticore

train_texts = [doc.split() for doc in trainds.preprocess_ctm(trainds.nonempty_text)]

# corpus 생성 (훈련 데이터를 이용)
train_corpus = [dictionary.doc2bow(text) for text in train_texts]

# LDA 모델 훈련
lda_model = LdaMulticore(
    corpus=train_corpus,
    num_topics=20,
    id2word=dictionary,
    passes=10,
    workers=3,  
    random_state=41
)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [67]:
# 테스트 데이터로부터 토픽 워드 리스트 생성
train_topics_lda = lda_model.get_document_topics(train_corpus, minimum_probability=0)

train_topic_words_list_lda = [
    [dictionary[word_id] for word_id, prob in lda_model.get_topic_terms(topicid, topn=10)]
    for topicid in range(lda_model.num_topics)
]
# 기존 사전에 LDA 모델에서 생성된 테스트 토픽의 단어 추가
for topic_words in train_topic_words_list_lda:
    dictionary.add_documents([topic_words])

topics = train_topic_words_list_lda

In [68]:
texts=reference_corpus
test_texts = [doc.split() for doc in testds.preprocess_ctm(testds.nonempty_text)]  # 예시 데이터셋
test_corpus = [dictionary.doc2bow(text) for text in texts]

In [69]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# 테스트 데이터셋의 토픽 분포 예측
test_topic_distributions = [lda_model.get_document_topics(bow) for bow in test_corpus]

# 테스트 데이터셋의 각 문서에 대해 가장 높은 토픽 할당
test_topic_labels_lda = [max(dist, key=lambda x: x[1])[0] for dist in test_topic_distributions]

# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels_lda, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels_lda).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels_lda[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)

# Original Mutual Information Score 계산
mi_score = mutual_info_score(test_topic_labels_lda, test_platform_labels)
print("Original Mutual Information Score:", mi_score)


Normalized Mutual Information (NMI): 0.22025558388915142
H(Y): 2.5345747318002294
H(Y|X): 2.134460722836188
Mutual Information (MI): 0.40011400896404137
Original Mutual Information Score: 0.4001140091303368


In [70]:
# 각 문서의 토픽 할당을 위한 함수
def assign_topics_to_documents(lda_model, corpus):
    topic_assignments = []
    for doc_bow in corpus:
        # 각 문서에 대한 토픽 분포를 얻음
        topic_distribution = lda_model.get_document_topics(doc_bow)
        # 가장 확률이 높은 토픽을 선택
        assigned_topic = max(topic_distribution, key=lambda x: x[1])[0]
        topic_assignments.append(assigned_topic)
    return topic_assignments

def calculate_label_purity(topic_labels):
    purity_scores = []
    
    for labels in topic_labels:
        if not labels:
            continue
        most_common_label = max(set(labels), key=labels.count) 
        purity = labels.count(most_common_label) / len(labels)
        purity_scores.append(purity)

    average_purity = sum(purity_scores) / len(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# 문서에 대한 토픽 할당
document_topics = assign_topics_to_documents(lda_model, train_corpus)

# 토픽별 라벨 데이터 수집 (라벨 데이터는 train_labels_list에 있다고 가정)
topic_labels_lda = [[] for _ in range(lda_model.num_topics)]
for doc_idx, topic in enumerate(document_topics):
    label = train_total_label_list[doc_idx]  # 문서에 해당하는 라벨
    topic_labels_lda[topic].append(label)

# label purity 계산
purity_scores_lda, average_purity_lda = calculate_label_purity(topic_labels_lda)

print("LDA 각 토픽의 라벨 순도:", purity_scores_lda)
print("LDA 평균 라벨 순도:", average_purity_lda)


LDA 각 토픽의 라벨 순도: [0.5376623376623376, 0.8157894736842105, 0.4634146341463415, 0.7651006711409396, 0.7421875, 0.4479166666666667, 0.6468085106382979, 0.375, 0.44329896907216493, 0.40625, 0.75, 0.38095238095238093, 0.36, 0.6578947368421053, 0.9305555555555556, 0.5321100917431193, 0.9413489736070382, 0.7540983606557377, 0.4107142857142857, 0.6129032258064516]
LDA 평균 라벨 순도: 0.5987003186943818


In [71]:
print(get_topic_coherence(topics, bbc_texts))

{'NPMI': 0.1642785645267926, 'UCI': 0.529567462391801, 'UMASS': -1.4069416879565713, 'CV': 0.6501009663416422, 'Topic_Diversity': 0.555}


In [72]:
print(get_topic_coherence(topics, nyt_texts))

{'NPMI': 0.4273957254341275, 'UCI': 2.221723490788759, 'UMASS': -1.544760010010628, 'CV': 0.609526215325179, 'Topic_Diversity': 0.555}


In [73]:
print(get_topic_coherence(topics, news_texts))

{'NPMI': 0.26796190895496735, 'UCI': 1.0816225937621762, 'UMASS': -1.6274273068295888, 'CV': 0.5866279068960474, 'Topic_Diversity': 0.555}


# BERTopic

In [76]:
from bertopic import BERTopic

bert_train_texts = [' '.join(doc) if isinstance(doc, list) else doc for doc in train_texts]

# BERTopic 모델 훈련
bertopic_model = BERTopic(language="english", calculate_probabilities=True, nr_topics=21, verbose=True)
bertopic_model.fit(bert_train_texts)

# 각 토픽별 상위 10개 단어 추출
topics = bertopic_model.get_topics()

# 상위 10개 단어를 포함하는 토픽 리스트 생성
topk_topic_words_list = []
for topic_num, topic in topics.items():
    if topic_num != -1:  # -1은 outlier 토픽을 의미합니다.
        topk_words = [word for word, _ in topic[:10]]
        topk_topic_words_list.append(topk_words)

2024-03-16 20:02:56,137 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/81 [00:00<?, ?it/s]

2024-03-16 20:02:58,511 - BERTopic - Embedding - Completed ✓
2024-03-16 20:02:58,512 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-16 20:03:12,070 - BERTopic - Dimensionality - Completed ✓
2024-03-16 20:03:12,072 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-16 20:03:12,316 - BERTopic - Cluster - Completed ✓
2024-03-16 20:03:12,317 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-16 20:03:12,836 - BERTopic - Representation - Completed ✓
2024-03-16 20:03:12,838 - BERTopic - Topic reduction - Reducing number of topics
2024-03-16 20:03:13,281 - BERTopic - Topic reduction - Reduced number of topics from 36 to 21


In [78]:
import numpy as np
import pandas as pd
from sklearn.metrics import mutual_info_score

# BERTopic 모델을 사용하여 테스트 데이터셋의 토픽 분포 예측
bert_test_texts = [' '.join(doc) if isinstance(doc, list) else doc for doc in test_texts]  # 테스트 데이터 준비
test_topics, probabilities = bertopic_model.transform(bert_test_texts)

test_topic_labels_bertopic = test_topics


# 플랫폼 라벨 준비
test_platform_labels = [testds[i][-1] for i in range(len(testds))]

# 플랫폼별 토픽 분포 계산
topic_dist_df_test = pd.crosstab(pd.Series(test_topic_labels_bertopic, name='Topic'),
                                 pd.Series(test_platform_labels, name='Platform'), normalize='index')

# 전체 데이터셋에 대한 토픽 분포의 엔트로피 계산 (H(Y))
topic_probabilities = pd.Series(test_topic_labels_bertopic).value_counts(normalize=True)
H_Y = -np.sum(topic_probabilities * np.log(topic_probabilities + 1e-10))

# 각 플랫폼별 조건부 엔트로피 계산 및 H(Y|X) 계산
H_Y_given_X_total = 0
platform_probabilities = pd.Series(test_platform_labels).value_counts(normalize=True)
for platform in platform_probabilities.index:
    platform_indices = [i for i, x in enumerate(test_platform_labels) if x == platform]
    platform_topic_labels = [test_topic_labels_bertopic[i] for i in platform_indices]
    platform_topic_prob = pd.Series(platform_topic_labels).value_counts(normalize=True)
    H_Y_given_X = -np.sum(platform_topic_prob * np.log(platform_topic_prob + 1e-10))
    H_Y_given_X_total += platform_probabilities[platform] * H_Y_given_X

# 상호정보량(MI) 계산
mi = H_Y - H_Y_given_X_total

# 플랫폼 분포의 엔트로피 H(X) 계산
H_X = -np.sum(platform_probabilities * np.log(platform_probabilities + 1e-10))

# 정규화된 상호정보량(NMI) 계산
NMI = 2 * mi / (H_Y + H_X)

print("Normalized Mutual Information (NMI):", NMI)
print('H(Y):', H_Y)
print('H(Y|X):', H_Y_given_X_total)
print('Mutual Information (MI):', mi)

# Original Mutual Information Score 계산
bertopic_mi_score = mutual_info_score(test_topic_labels_bertopic, test_platform_labels)
print("Mutual Information Score with BERTopic:", bertopic_mi_score)


Batches:   0%|          | 0/23 [00:00<?, ?it/s]

2024-03-16 20:03:43,910 - BERTopic - Dimensionality - Reducing dimensionality of input embeddings.
2024-03-16 20:03:54,174 - BERTopic - Dimensionality - Completed ✓
2024-03-16 20:03:54,175 - BERTopic - Clustering - Approximating new points with `hdbscan_model`
2024-03-16 20:03:54,202 - BERTopic - Probabilities - Start calculation of probabilities with HDBSCAN
2024-03-16 20:03:54,294 - BERTopic - Probabilities - Completed ✓
2024-03-16 20:03:54,295 - BERTopic - Cluster - Completed ✓


Normalized Mutual Information (NMI): 0.3418678856708719
H(Y): 2.2057741930847343
H(Y|X): 1.6409437106873197
Mutual Information (MI): 0.5648304823974146
Mutual Information Score with BERTopic: 0.5648304831979718


In [82]:
label_to_num = {'politics': 0, 'sport': 1, 'tech': 2}

# BERTopic 모델 훈련
bertopic_model = BERTopic(language="english", calculate_probabilities=True, verbose=True, nr_topics=21)
bertopic_model.fit(bert_train_texts)

# 테스트 데이터셋의 토픽 할당
topics, probs = bertopic_model.transform(bert_test_texts)

# 토픽별 문서 수 계산 (노이즈 토픽 -1 제외)
topic_counts = Counter(topics)

# 노이즈 토픽(-1) 포함 상위 21개 토픽 선택
top_21_topics = [topic for topic, count in topic_counts.most_common(21)]

# 노이즈 토픽 제거
if -1 in top_21_topics:
    top_21_topics.remove(-1)
test_target_bert = [label_to_num[label] for label in test_total_label_list]

# 상위 토픽에 해당하는 문서의 확률과 라벨만 필터링 (노이즈 토픽 제외)
filtered_probs = np.array([probs[i] for i, topic in enumerate(topics) if topic in top_21_topics])
filtered_labels = [test_target_bert[i] for i, topic in enumerate(topics) if topic in top_21_topics]

def calculate_label_purity(filtered_labels, top_20_topics, topics):
    """
    각 토픽의 label purity를 계산합니다.
    
    :param filtered_labels: 상위 20개 토픽에 해당하는 문서의 라벨
    :param top_20_topics: 상위 20개 토픽의 ID 리스트
    :param topics: 모든 문서에 할당된 토픽 ID 리스트
    :return: 각 토픽의 label purity 리스트와 평균 label purity
    """
    topic_label_mapping = {topic: [] for topic in top_20_topics}
    
    # 각 토픽에 대한 라벨 할당
    for label, topic in zip(filtered_labels, topics):
        if topic in top_20_topics:
            topic_label_mapping[topic].append(label)
    
    purity_scores = []
    for topic, labels in topic_label_mapping.items():
        if labels:
            most_common_label, count = Counter(labels).most_common(1)[0]
            purity = count / len(labels)
            purity_scores.append(purity)
    
    average_purity = np.mean(purity_scores) if purity_scores else 0
    return purity_scores, average_purity

# BERTopic에 대한 label purity 계산
purity_scores_bertopic, average_purity_bertopic = calculate_label_purity(filtered_labels, top_21_topics, topics)

print("BERTopic 각 토픽의 label purity:", purity_scores_bertopic)
print("BERTopic 평균 label purity:", average_purity_bertopic)

2024-03-16 20:31:07,256 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/81 [00:00<?, ?it/s]

2024-03-16 20:31:10,266 - BERTopic - Embedding - Completed ✓
2024-03-16 20:31:10,268 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-03-16 20:31:25,242 - BERTopic - Dimensionality - Completed ✓
2024-03-16 20:31:25,244 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-03-16 20:31:25,448 - BERTopic - Cluster - Completed ✓
2024-03-16 20:31:25,449 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-03-16 20:31:25,959 - BERTopic - Representation - Completed ✓
2024-03-16 20:31:25,961 - BERTopic - Topic reduction - Reducing number of topics
2024-03-16 20:31:26,486 - BERTopic - Topic reduction - Reduced number of topics from 27 to 21


Batches:   0%|          | 0/23 [00:00<?, ?it/s]

2024-03-16 20:31:27,374 - BERTopic - Dimensionality - Reducing dimensionality of input embeddings.
2024-03-16 20:31:34,295 - BERTopic - Dimensionality - Completed ✓
2024-03-16 20:31:34,296 - BERTopic - Clustering - Approximating new points with `hdbscan_model`
2024-03-16 20:31:34,325 - BERTopic - Probabilities - Start calculation of probabilities with HDBSCAN
2024-03-16 20:31:34,412 - BERTopic - Probabilities - Completed ✓
2024-03-16 20:31:34,413 - BERTopic - Cluster - Completed ✓


BERTopic 각 토픽의 label purity: [0.5271317829457365, 0.8902439024390244, 0.9047619047619048, 1.0, 1.0, 0.6666666666666666, 0.95, 1.0, 1.0, 0.6666666666666666, 1.0, 0.5, 1.0, 0.75, 0.6666666666666666]
BERTopic 평균 label purity: 0.8348091726764443


In [79]:
print(get_topic_coherence(topk_topic_words_list, bbc_texts))

{'NPMI': 0.23020391288958683, 'UCI': 0.968936293856757, 'UMASS': -1.6079016263460923, 'CV': 0.6510047177661524, 'Topic_Diversity': 0.9}


In [80]:
print(get_topic_coherence(topk_topic_words_list, nyt_texts))

{'NPMI': 0.5322848500640807, 'UCI': 2.840653976306891, 'UMASS': -1.3006571104419338, 'CV': 0.6605895825589053, 'Topic_Diversity': 0.9}


In [81]:
print(get_topic_coherence(topk_topic_words_list, news_texts))

{'NPMI': 0.3944021842637414, 'UCI': 1.9556340161079062, 'UMASS': -1.594138517863992, 'CV': 0.5961484132697848, 'Topic_Diversity': 0.9}
